# Firearm Background Checks and Mortality Rates
## Dana Laufer

In [1]:
import pandas as pd
import numpy as np
import altair as alt

In [2]:
pd.set_option("display.max_columns", None)

In [3]:
# Load in the data
background_data = pd.read_csv("firearms.csv")
mortality_data = pd.read_csv('mortality.csv')

# Data Processing and Transforming

In [4]:
background_data.head()

month       state   permit  permit_recheck  handgun  long_gun   other  \
0  2020-05     Alabama  28064.0           534.0  32394.0   13899.0  1468.0   
1  2020-05      Alaska     55.0           218.0   4469.0    3196.0   429.0   
2  2020-05     Arizona   4737.0           577.0  28089.0   11334.0  2053.0   
3  2020-05    Arkansas   3868.0           603.0  11572.0    7005.0   528.0   
4  2020-05  California  23948.0             0.0  50811.0   28550.0  6499.0   

   multiple  admin  prepawn_handgun  prepawn_long_gun  prepawn_other  \
0      1016    0.0             21.0              17.0            5.0   
1       219    0.0              1.0               2.0            0.0   
2      2402    0.0              9.0               8.0            3.0   
3       453    4.0             17.0              12.0            1.0   
4         0    0.0              0.0               0.0            0.0   

   redemption_handgun  redemption_long_gun  redemption_other  \
0              1853.0               1162.0              13.0   
1               131.0                 99.0               0.0   
2              1089.0                654.0               8.0   
3               824.0                995.0               2.0   
4               575.0                437.0               3.0   

   returned_handgun  returned_long_gun  returned_other  rentals_handgun  \
0               2.0                0.0             0.0              0.0   
1              35.0               14.0             0.0              0.0   
2             101.0               12.0             1.0              0.0   
3               0.0                0.0             0.0              0.0   
4               0.0                0.0             0.0              0.0   

   rentals_long_gun  private_sale_handgun  private_sale_long_gun  \
0               0.0                  38.0                   23.0   
1               0.0                   8.0                    5.0   
2               0.0                  10.0                   10.0   
3               0.0                  14.0                   15.0   
4               0.0                   0.0                    0.0   

   private_sale_other  return_to_seller_handgun  return_to_seller_long_gun  \
0                 8.0                       1.0                        1.0   
1                 2.0                       0.0                        0.0   
2                 1.0                       0.0                        0.0   
3                 4.0                       0.0                        0.0   
4                 0.0                       0.0                        0.0   

   return_to_seller_other  totals  
0                     0.0   80519  
1                     0.0    8883  
2                     0.0   51098  
3                     0.0   25917  
4                     0.0  110823

In [5]:
mortality_data.head()

State    Year  Deaths  Population  Crude Rate
0  Alabama  1999.0     790     4430141        17.8
1  Alabama  2000.0     766     4447100        17.2
2  Alabama  2001.0     737     4467634        16.5
3  Alabama  2002.0     724     4480089        16.2
4  Alabama  2003.0     765     4503491        17.0

In [6]:
mortality_data.columns = mortality_data.columns.str.lower()
mortality_data.dropna(inplace = True)
mortality_data.loc[:, 'year'] = mortality_data.loc[:, 'year'].astype(int)
mortality_data.loc[:, 'year'] = mortality_data.loc[:, 'year'].astype(str)

In [7]:
background_data.fillna(0, inplace = True)
background_data.rename(columns = {"month": "date"}, inplace = True)

# Split the date into month and year
background_data[['year','month']] = background_data.date.str.split(pat = "-", expand=True)

# Reorder the columns
cols = [background_data.columns[-1]] + [col for col in background_data if col != background_data.columns[-1]]
cols = [cols[-1]] + [col for col in cols if col != cols[-1]]
background_data = background_data[cols]

# Estimate sales
background_data.loc[:, 'sales'] = background_data.loc[:, ['handgun', 'long_gun', 'other', 'multiple', 'multiple']].sum(axis = 1)

In [8]:
# Mortality data only has years, so transform background data 
background_data_per_year = background_data.groupby(['year', 'state'], as_index = False).sum()

# Mortality data only has data from 1999 to 2018
data_combined = background_data_per_year.query('year != "2020" & year != "2019" & year != "1998"')
data_combined = data_combined.merge(mortality_data)

data_combined_year = data_combined.groupby('year', as_index = False).sum()

In [9]:
# Make new variables with population parameter
data_combined.loc[:, 'total_rate'] = data_combined['totals']*100000/data_combined['population']
data_combined.loc[:, 'sale_rate'] = data_combined['sales']*100000/data_combined['population']
data_combined

year          state    permit  permit_recheck   handgun  long_gun  \
0     1999        Alabama       0.0             0.0   94544.0  149017.0   
1     1999         Alaska       2.0             0.0   14339.0   27790.0   
2     1999        Arizona   20503.0             0.0   78103.0   71365.0   
3     1999       Arkansas    4271.0             0.0   50523.0  126875.0   
4     1999     California  101132.0             0.0  371893.0  410119.0   
...    ...            ...       ...             ...       ...       ...   
1015  2018       Virginia   18450.0           305.0  253744.0  168859.0   
1016  2018     Washington  177654.0           736.0  202826.0  148345.0   
1017  2018  West Virginia   52481.0             0.0   75539.0   76310.0   
1018  2018      Wisconsin  131991.0             2.0  155441.0  145652.0   
1019  2018        Wyoming    6007.0           109.0   21617.0   24978.0   

        other  multiple  admin  prepawn_handgun  prepawn_long_gun  \
0         0.0      3195    0.0              0.0               0.0   
1         0.0       942    0.0              0.0               0.0   
2         0.0      3453  124.0              0.0               0.0   
3         0.0      2946    1.0              0.0               0.0   
4         0.0         0    0.0              0.0               0.0   
...       ...       ...    ...              ...               ...   
1015  34835.0         0    0.0              0.0               0.0   
1016  33596.0      9382   24.0            162.0             158.0   
1017   4213.0      4892   84.0            155.0             174.0   
1018  12339.0       583    1.0              0.0              13.0   
1019   1625.0      1358   63.0             29.0              42.0   

      prepawn_other  redemption_handgun  redemption_long_gun  \
0               0.0                 0.0                  0.0   
1               0.0                 0.0                  0.0   
2               0.0                 0.0                  0.0   
3               0.0                 0.0                  0.0   
4               0.0                 0.0                  0.0   
...             ...                 ...                  ...   
1015            0.0                 0.0                  0.0   
1016           33.0             14738.0              12222.0   
1017            1.0             12545.0              14418.0   
1018           86.0              1645.0               3019.0   
1019            2.0              1812.0               2255.0   

      redemption_other  returned_handgun  returned_long_gun  returned_other  \
0                  0.0               0.0                0.0             0.0   
1                  0.0               0.0                0.0             0.0   
2                  0.0               0.0                0.0             0.0   
3                  0.0               0.0                0.0             0.0   
4                  0.0               0.0                0.0             0.0   
...                ...               ...                ...             ...   
1015               0.0             472.0               88.0             7.0   
1016             177.0            5619.0             1370.0           136.0   
1017              21.0             131.0               10.0            17.0   
1018              64.0            1103.0              335.0            26.0   
1019              21.0               3.0                0.0             0.0   

      rentals_handgun  rentals_long_gun  private_sale_handgun  \
0                 0.0               0.0                   0.0   
1                 0.0               0.0                   0.0   
2                 0.0               0.0                   0.0   
3                 0.0               0.0                   0.0   
4                 0.0               0.0                   0.0   
...               ...               ...                   ...   
1015              0.0               0.0                   0.0   
1016              0.0               0.

In [10]:
# Make new variables divided by population
data_combined_year.loc[:, 'total_rate'] = data_combined_year['totals']*100000/data_combined_year['population']
data_combined_year.loc[:, 'sale_rate'] = data_combined_year['sales']*100000/data_combined_year['population']
data_combined_year

year      permit  permit_recheck    handgun   long_gun     other  \
0   1999   1037700.0             0.0  2532530.0  5216322.0       0.0   
1   2000   1227814.0             0.0  2187598.0  4778762.0       0.0   
2   2001   1408338.0             0.0  2161178.0  4941987.0       0.0   
3   2002   1363211.0             0.0  1838245.0  4407867.0       0.0   
4   2003   1403496.0             0.0  1844608.0  4381438.0       0.0   
5   2004   1345672.0             0.0  1984078.0  4505326.0       0.0   
6   2005   1350193.0             0.0  2234190.0  4582777.0       0.0   
7   2006   2036569.0             0.0  2434092.0  4787879.0       0.0   
8   2007   3077655.0             0.0  2628665.0  4568878.0       0.0   
9   2008   3697854.0             0.0  3325522.0  4906513.0       0.0   
10  2009   4449333.0             0.0  3682774.0  4976959.0   23164.0   
11  2010   4882950.0             0.0  3671163.0  4840422.0   52717.0   
12  2011   5544418.0             0.0  4291490.0  5443852.0   70059.0   
13  2012   5683545.0             0.0  5669388.0  6863391.0  162697.0   
14  2013   6168970.0             0.0  6372832.0  7125535.0  212501.0   
15  2014   7768805.0             0.0  6185027.0  5540246.0  267854.0   
16  2015   8780966.0             0.0  7319354.0  5476520.0  329062.0   
17  2016  11133892.0        519265.0  8071204.0  5985362.0  585682.0   
18  2017   9940828.0       1046410.0  7210234.0  5231671.0  399243.0   
19  2018  10228228.0       2424274.0  6549408.0  4913578.0  492805.0   

    multiple     admin  prepawn_handgun  prepawn_long_gun  prepawn_other  \
0     103669  148115.0              0.0               0.0            0.0   
1      95681  131648.0              0.0               0.0            0.0   
2      96984  100126.0           1274.0            3266.0            0.0   
3      92892   76776.0           5082.0           11080.0            0.0   
4      99034   69946.0           5146.0            8656.0            0.0   
5     101737   51559.0           3943.0            6459.0            0.0   
6     109549   13158.0           3151.0            5782.0            0.0   
7     129899   41792.0           3146.0            5917.0            0.0   
8     324193   27318.0           2901.0            5504.0            0.0   
9     186891   13883.0           2330.0            4205.0            0.0   
10    235469    7302.0           2831.0            4846.0            0.0   
11    180396    6751.0           3128.0            5175.0           28.0   
12    219355   11912.0           3161.0            4489.0           17.0   
13    229928    6670.0           2927.0            3961.0           38.0   
14    241005    5663.0           2500.0            3418.0           89.0   
15    225066    4258.0           2225.0            2822.0          146.0   
16    242062    7037.0           2361.0            2531.0          175.0   
17    257376    3366.0           2621.0            2563.0          161.0   
18    235754    5643.0           3213.0            2896.0          290.0   
19    256650   14767.0           4344.0            3454.0          436.0   

    redemption_handgun  redemption_long_gun  redemption_other  \
0                  0.0                  0.0               0.0   
1                  0.0                  0.0               0.0   
2              26999.0              72322.0               0.0   
3             171051.0             392377.0               0.0   
4             181927.0             399702.0               0.0   
5             182539.0             390427.0               0.0   
6             183116.0             375703.0               0.0   
7             186385.0             356847.0               0.0   
8             180790.0             336230.0               0.0   
9             199205.0             348096.0               0.0   
10            222523.0             369491.0               0.0   
11            260441.0             406680.0             424.0   
12            298167.0             435954.0      

# Exploratory Analysis

In [11]:
alt.Chart(data_combined).mark_boxplot().encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('totals', title = 'Total Background Checks')
).properties(
    title = "Total Background Checks by Year"
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
)


alt.Chart(...)

In [12]:
alt.Chart(data_combined).mark_line().encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('totals', title = 'Total Background Checks'),
    color = 'state'
).properties(
    title = "Total Background Checks by Year"
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
).configure_legend(
    labelFontSize = 8,
    titleOpacity = 0,
    labelLimit = 500
)


alt.Chart(...)

In [13]:
alt.Chart(data_combined).mark_line().encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('sales', title = 'Estimated Firearm Sales'),
    color = 'state'
).properties(
    title = "Estimated Firearm Sales by Year and State"
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
).configure_legend(
    labelFontSize = 8,
    titleOpacity = 0,
    labelLimit = 500
)


alt.Chart(...)

In [14]:
alt.Chart(data_combined).mark_line().encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('sale_rate', title = 'Firearm Sales per 100,000'),
    color = 'state'
).properties(
    title = "Estimated Firearm Sales by Year and State per 100,000"
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
).configure_legend(
    labelFontSize = 8,
    titleOpacity = 0,
    labelLimit = 500
)


alt.Chart(...)

In [15]:
chart1 = alt.Chart(data_combined_year).mark_line(color = '#d62728').encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('deaths', title = "Number of Deaths from Firearms", axis = alt.Axis(titleColor = '#d62728'))
)

chart2 = alt.Chart(data_combined_year).mark_line(color = '#1f77b4', clip = True).encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('sales', title = 'Firearm Sales', axis = alt.Axis(titleColor = '#1f77b4'))
)

chart1 + chart2


alt.layer(chart1, chart2).resolve_scale(y = 'independent').properties(
    title = "Estimated Firearm Sales and Firearm Deaths per Year",
    width = 500
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
)

alt.LayerChart(...)

In [16]:
chart1 = alt.Chart(data_combined_year).mark_line(color = '#d62728').encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('crude rate', title = "Deaths from Firearms per 100,000", axis = alt.Axis(titleColor = '#d62728'))
)

chart2 = alt.Chart(data_combined_year).mark_line(color = '#1f77b4', clip = True).encode(
    x = alt.X('year', title = 'Year'),
    y = alt.Y('sale_rate', title = 'Estimated Firearm Sales per 100,000', axis = alt.Axis(titleColor = '#1f77b4'))
)

chart1 + chart2


alt.layer(chart1, chart2).resolve_scale(y = 'independent').properties(
    title = "Estimated Firearm Sales and Firearm Deaths per 100,000",
    width = 500
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
)

alt.LayerChart(...)

In [17]:
chart = alt.Chart(data_combined).mark_point().encode(
    x = 'sale_rate',
    y = 'crude rate'
)

chart + chart.transform_regression('sale_rate', 'crude rate').mark_line(color="red")

alt.LayerChart(...)

# Principal Component Analysis

In [18]:
# Create dataframe indexed by state, with columns for every year containing sale rates data 
data_states = data_combined.groupby(['year', 'state'], as_index = False).sum()
data_states.set_index('state', inplace = True)
data_states = data_states.pivot(columns = 'year', values = 'sale_rate')

In [19]:
# Center and align the data
means = np.mean(data_states, axis = 0)
std = np.std(data_states, axis = 0)
data_states_centered = data_states - means
data_states_aligned = data_states_centered/std
data_states_aligned

year                      1999      2000      2001      2002      2003  \
state                                                                    
Alabama               1.018127  0.896363  0.881964  0.826140  0.867361   
Alaska                1.701905  1.620964  1.541836  1.485907  1.458296   
Arizona              -0.215051 -0.297718 -0.341349 -0.400668 -0.529468   
Arkansas              1.637151  1.454810  1.255748  0.987212  0.969777   
California           -0.594466 -0.687758 -0.734368 -0.908109 -1.162761   
Colorado              1.301888  2.051773  2.387886  0.861357  0.666578   
Connecticut          -1.079380 -1.611313 -1.283761 -0.820537 -0.813348   
Delaware             -0.613309 -0.632114 -0.577096 -0.497231 -0.540511   
District of Columbia -1.730786 -1.610015 -1.621878 -1.818127 -1.833125   
Florida              -0.910764 -0.822228 -0.729326 -0.747561 -0.738026   
Georgia              -0.208996 -0.281724 -0.344945 -0.337356 -0.356411   
Hawaii               -1.732420 -1.611488 -1.623345 -1.818914 -1.834368   
Idaho                 1.096847  0.993251  0.832186  0.676305  0.606594   
Illinois             -0.980796 -0.991222 -0.998783 -1.044653 -1.040715   
Indiana              -0.093216 -0.674458 -0.881572 -0.974941 -0.731845   
Iowa                 -0.962217 -0.891689 -0.921900 -0.970643 -0.908621   
Kansas                0.233592  0.205368  0.127699  0.226086  0.268529   
Kentucky              1.333144  1.261440  1.257090  1.254813  1.184070   
Louisiana             0.437054  0.352621  0.312448  0.236754  0.305132   
Maine                 0.109563  0.162520  0.324584  0.574986  0.590311   
Maryland             -1.232028 -1.158079 -1.134474 -1.239461 -1.256772   
Massachusetts        -1.580764 -1.412233 -1.392174 -1.476617 -1.439487   
Michigan             -0.825804 -0.720158 -0.696253 -0.543962 -0.523514   
Minnesota            -0.242085 -0.066330 -0.099676  0.067925  0.278606   
Mississippi           1.442241  1.281463  1.063917  0.846020  0.844256   
Missouri              0.095076  0.098561  0.108165  0.202190  0.226928   
Montana               2.304353  2.361704  2.341938  2.362650  2.511060   
Nebraska             -0.828955 -0.754932 -0.796386 -0.844486 -0.815639   
Nevada               -0.111834 -0.341925 -0.397716 -0.381227 -0.383153   
New Hampshire        -0.223868 -0.019821  0.037949  0.201309  0.173760   
New Jersey           -1.504396 -1.389781 -1.389439 -1.488329 -1.518132   
New Mexico            0.864808  0.721574  0.630847  0.420570  0.359726   
New York             -1.424664 -1.324817 -1.315184 -1.443329 -1.457075   
North Carolina       -0.489189 -0.450152 -0.485227 -0.705897 -0.711409   
North Dakota          0.530374  0.727144  0.703622  0.947890  1.046813   
Ohio                 -0.429192 -0.390191 -0.343988 -0.218479 -0.232363   
Oklahoma              0.719380  0.690457  0.677619  0.557959  0.668411   
Oregon                0.598427  0.377825  0.423427  0.737713  0.794091   
Pennsylvania          0.444664  0.350624  0.438435  1.150494  0.848636   
Rhode Island         -1.197904 -1.120278 -1.097892 -1.191603 -1.200022   
South Carolina        0.000134 -0.099762 -0.195546 -0.318250 -0.321494   
South Dakota          0.316482  0.817955  1.041070  1.663864  1.879847   
Tennessee             0.583221  0.462478  0.395753  0.699187  0.621987   
Texas                -0.167233 -0.196551 -0.249770 -0.401154 -0.414051   
Utah                  0.012918 -0.099464 -0.137758 -0.084998 -0.082243   
Vermont               0.075233  0.054550  0.065368  0.354089  0.272196   
Virginia             -0.268267 -0.278466 -0.259284 -0.104852 -0.068277   
Washington           -0.716622 -0.638272 -0.568847 -0.503685 -0.366947   
West Virginia         1.940010  1.959926  2.094549  2.026190  1.876611   
Wisconsin            -0.092077  0.057137  0.040855  0.212859  0.347298   
Wyoming               1.659693  1.612433  1.632979  1.704598  1.612902   

year                      2004      2005      2006      2007      2008  \
sta

In [20]:
# Perform SVD
u, s, vt = np.linalg.svd(data_states_aligned, full_matrices = False)
first_2_pcs = (data_states_aligned @ vt.T).loc[:, [0,1]]
first_2_pcs.columns = ['pc1', 'pc2']
first_2_pcs = first_2_pcs.reset_index(drop = True)

In [21]:
state_names = list(data_states.index)
first_2_pcs['state'] = state_names

alt.Chart(first_2_pcs).mark_text().encode(
    x = 'pc1',
    y = 'pc2',
    text = 'state'
).properties(width=450).interactive()

alt.Chart(...)

In [22]:
brush = alt.selection(type='interval')

labels = alt.Chart(first_2_pcs).mark_text().encode(
 x = alt.X('pc1', title = "First Principal Component"),
 y = alt.Y('pc2', title = "Second Principal Component"),
 text = 'state',
 color = alt.condition(brush, alt.value('blue'), alt.value('grey'))
).properties(width=450).add_selection(brush)

# Base chart for data tables
ranked_text = alt.Chart(first_2_pcs).mark_text().encode(
    y = alt.Y('row_number:O', axis = None)
).transform_window(
    row_number='row_number()'
).transform_filter(
    brush
).transform_window(
    rank='rank(row_number)'
).transform_filter(
    alt.datum.rank<20
)

# Data Tables
origin = ranked_text.encode(text = 'state:N').properties(title = 'State', width=100)
                                                         
# Build chart
alt.hconcat(
    labels,origin
).properties(
    title = "Firearm Sales per 100,000 Principal Component Analysis"
)

alt.HConcatChart(...)

In [23]:
df = pd.DataFrame({'v':vt[0, :], 'Column names':list(data_states.columns)})

alt.Chart(df).mark_bar().encode(
    x = 'Column names',
    y = alt.Y('v', title = ""),
    opacity=alt.value(0.7)
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_axisX(
    labelAngle = 0
).properties(title = "Scalar Multiplied by Each Column for First PCA", width = 700)


alt.Chart(...)

In [24]:
df = pd.DataFrame({'v':vt[1, :], 'Column names':list(data_states.columns)})
alt.Chart(df).mark_bar().encode(
 x='Column names',
 y='v',
 opacity=alt.value(0.7)
 ).configure_axis(
 labelFontSize=12,
 titleFontSize=14
 ).configure_axisX(
 labelAngle = 0
 ).properties(width = 700)


alt.Chart(...)

In [25]:
explained_var = pd.DataFrame({
 'PC #': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
 'Fraction of Variance Explained' : s[range(0,10)]**2/sum(s**2)
})
# Draw your Altair visualization
alt.Chart(explained_var,
 title = "Variance Explained by Principal Components"
).mark_bar(size=30).encode(
 alt.X('PC #:O'),
 alt.Y('Fraction of Variance Explained:Q')
).configure_axisX(labelAngle=0).properties(width=500)


alt.Chart(...)

# Regression Model

In [26]:
X = data_combined[['sale_rate']]
Y = data_combined.loc[:, 'crude rate']

In [27]:
from sklearn import linear_model as lm
linear_model = lm.LinearRegression()

In [28]:
# Fit the linear model
linear_model.fit(X, Y)

# Generate predictions
Y_hat = linear_model.predict(X)

# Coefficients in the linear regression model
coefs = linear_model.coef_
intercept = linear_model.intercept_
print("Y intercept:", intercept, "\nSlope:", coefs)

Y intercept: 7.890055727489272 
Slope: [0.00095711]


In [29]:
regression = pd.DataFrame({'x': data_combined['sale_rate'], 'y': Y_hat})

chart1 = alt.Chart(data_combined).mark_point().encode(
    x = alt.X('sale_rate', title = 'Firearm Sales per 100,000'),
    y = alt.Y('crude rate', title = 'Firearm Deaths per 100,000')
)

chart2 = alt.Chart(regression).mark_line(color = 'red').encode(
    x = 'x',
    y = 'y'
)

alt.layer(chart1 + chart2).properties(
    title = "Estimated Firearm Sales and Firearm Deaths per 100,000",
    width = 500
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
)


alt.LayerChart(...)

In [30]:
residuals = pd.DataFrame({'True Deaths per 100,000': Y, 'Residuals': Y - Y_hat})

alt.Chart(residuals, title = "Residual Plot of Deaths by Firearm per 100,000").mark_point().encode(
    y = 'Residuals',
    x = 'True Deaths per 100,000'
).configure_axis(
 labelFontSize = 12,
 titleFontSize = 16
).configure_title(
 fontSize = 17
)

alt.Chart(...)

In [31]:
from sklearn.metrics import mean_squared_error as mse

rmse = np.sqrt(mse(Y, Y_hat))
print("Root mean squared error:", rmse)

Root mean squared error: 3.942136777472344


There's lots of sales rates very close to zero, so I'm going to get rid of these outliers and see if my model improves.

In [32]:
data_narrowed = data_combined.query('sale_rate > 150')

X_narrow = data_narrowed[['sale_rate']]
Y_narrow = data_narrowed.loc[:, 'crude rate']

data_combined

year          state    permit  permit_recheck   handgun  long_gun  \
0     1999        Alabama       0.0             0.0   94544.0  149017.0   
1     1999         Alaska       2.0             0.0   14339.0   27790.0   
2     1999        Arizona   20503.0             0.0   78103.0   71365.0   
3     1999       Arkansas    4271.0             0.0   50523.0  126875.0   
4     1999     California  101132.0             0.0  371893.0  410119.0   
...    ...            ...       ...             ...       ...       ...   
1015  2018       Virginia   18450.0           305.0  253744.0  168859.0   
1016  2018     Washington  177654.0           736.0  202826.0  148345.0   
1017  2018  West Virginia   52481.0             0.0   75539.0   76310.0   
1018  2018      Wisconsin  131991.0             2.0  155441.0  145652.0   
1019  2018        Wyoming    6007.0           109.0   21617.0   24978.0   

        other  multiple  admin  prepawn_handgun  prepawn_long_gun  \
0         0.0      3195    0.0              0.0               0.0   
1         0.0       942    0.0              0.0               0.0   
2         0.0      3453  124.0              0.0               0.0   
3         0.0      2946    1.0              0.0               0.0   
4         0.0         0    0.0              0.0               0.0   
...       ...       ...    ...              ...               ...   
1015  34835.0         0    0.0              0.0               0.0   
1016  33596.0      9382   24.0            162.0             158.0   
1017   4213.0      4892   84.0            155.0             174.0   
1018  12339.0       583    1.0              0.0              13.0   
1019   1625.0      1358   63.0             29.0              42.0   

      prepawn_other  redemption_handgun  redemption_long_gun  \
0               0.0                 0.0                  0.0   
1               0.0                 0.0                  0.0   
2               0.0                 0.0                  0.0   
3               0.0                 0.0                  0.0   
4               0.0                 0.0                  0.0   
...             ...                 ...                  ...   
1015            0.0                 0.0                  0.0   
1016           33.0             14738.0              12222.0   
1017            1.0             12545.0              14418.0   
1018           86.0              1645.0               3019.0   
1019            2.0              1812.0               2255.0   

      redemption_other  returned_handgun  returned_long_gun  returned_other  \
0                  0.0               0.0                0.0             0.0   
1                  0.0               0.0                0.0             0.0   
2                  0.0               0.0                0.0             0.0   
3                  0.0               0.0                0.0             0.0   
4                  0.0               0.0                0.0             0.0   
...                ...               ...                ...             ...   
1015               0.0             472.0               88.0             7.0   
1016             177.0            5619.0             1370.0           136.0   
1017              21.0             131.0               10.0            17.0   
1018              64.0            1103.0              335.0            26.0   
1019              21.0               3.0                0.0             0.0   

      rentals_handgun  rentals_long_gun  private_sale_handgun  \
0                 0.0               0.0                   0.0   
1                 0.0               0.0                   0.0   
2                 0.0               0.0                   0.0   
3                 0.0               0.0                   0.0   
4                 0.0               0.0                   0.0   
...               ...               ...                   ...   
1015              0.0               0.0                   0.0   
1016              0.0               0.

In [33]:
# Fit the linear model
linear_model.fit(X_narrow, Y_narrow)

# Generate predictions
Y_hat_narrow = linear_model.predict(X_narrow)

# Coefficients in the linear regression model
coefs_narrow = linear_model.coef_
intercept_narrow = linear_model.intercept_
print("Y intercept:", intercept_narrow, "\nSlope:", coefs_narrow)

Y intercept: 7.169716097053719 
Slope: [0.00108975]


In [34]:
regression_narrow = pd.DataFrame({'x': data_narrowed['sale_rate'], 'y': Y_hat_narrow})

chart1 = alt.Chart(data_narrowed).mark_point().encode(
    x = alt.X('sale_rate', title = 'Firearm Sales per 100,000'),
    y = alt.Y('crude rate', title = 'Firearm Deaths per 100,000')
)

chart2 = alt.Chart(regression_narrow).mark_line(color = 'red').encode(
    x = 'x',
    y = 'y'
)

alt.layer(chart1 + chart2).properties(
    title = "Estimated Firearm Sales and Firearm Deaths per 100,000",
    width = 500
).configure_title(fontSize = 18).configure_axis(
    titleFontSize = 16,
    labelFontSize = 14
)


alt.LayerChart(...)

In [35]:
residuals = pd.DataFrame({'True Deaths per 100,000': Y, 'Residuals': Y - Y_hat})

alt.Chart(residuals, title = "Residual Plot of Deaths by Firearm per 100,000").mark_point().encode(
    y = 'Residuals',
    x = 'True Deaths per 100,000'
).configure_axis(
 labelFontSize = 12,
 titleFontSize = 16
).configure_title(
 fontSize = 17
)

alt.Chart(...)

In [36]:
rmse_narrow = np.sqrt(mse(Y_narrow, Y_hat_narrow))
print("Root mean squared error:", rmse_narrow)

Root mean squared error: 3.3390103136704723
